## Security Analytics ##

In [1]:
import requests
import IPython.display as display
from googleapiclient import discovery
import json
import time
from langdetect import detect
import pandas as pd
import numpy as np


In [11]:
# setting up api client
from googleapiclient import discovery
import itertools
api_keys = []
api_key_cycle = itertools.cycle(api_keys)


In [3]:
import pandas as pd

#csv_files2 = ['20230401_Ukraine.csv', '20230402_Ukraine.csv', '20230403_Ukraine.csv', '20230404_Ukraine.csv', '20230405_Ukraine.csv', '20230406_Ukraine.csv', '20230407_Ukraine.csv']
csv_files = ['20220819.csv', '20220830.csv', '20220901.csv', '20220915.csv', '20221001.csv', '20221015.csv', '20221101.csv', '20221115.csv', '20221201.csv', '20221215.csv', '20230101.csv', '20230115.csv', '20230201.csv', '20230215.csv', '20230301.csv', '20230315.csv', '20230401.csv', '20230415.csv', '20230501.csv', '20230506.csv']

dfs = []

for file in csv_files:
    df = pd.read_csv(file)
    dfs.append(df)


/var/folders/l6/gg22yf1j64zgklq5qqv9httm0000gn/T/ipykernel_73043/2790099794.py:9: DtypeWarning: Columns (15) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv(file)
/var/folders/l6/gg22yf1j64zgklq5qqv9httm0000gn/T/ipykernel_73043/2790099794.py:9: DtypeWarning: Columns (15) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv(file)


In [4]:
combined_df = pd.concat(dfs, ignore_index=True)


In [5]:
sample_df = combined_df.sample(n=150000, random_state=123)
#print(sample_df.head())
print(sample_df['text'])
print(sample_df.shape)
sample_df.to_csv('INITIAL150000short0819t0506.csv', index=False)

1117804    🇷🇺 Le drapeau de la PMC Wagner flotte sur le c...
943525     Awaited Delivery of President's Sweatshirt fro...
1132897    ‼️ Please share this video. \nHopefully, someo...
579216     #NATO Headquarters held its first-ever Climate...
1138976    Listen 📢 https://t.co/4fiTdRAQna #Ukraine russ...
                                 ...                        
1165660    Ruský projekt velké zimní ofenzívy na Donbasu ...
882404     #Vikings star, actress, director and producer,...
223520     Tras el conflicto ocurrido entre Rusia y Ucran...
218417     Ravens RB J.K. Dobbins was a full participant ...
600831     "Let's have a photo-trip at  #Bakhmut" they sa...
Name: text, Length: 150000, dtype: object
(150000, 29)


In [7]:
def call_perspective_api(text, client, api_key, language='en'):
    analyze_request = {
        'comment': {'text': text},
        'languages': [language],
        'requestedAttributes': {
            "SEVERE_TOXICITY": {},
            "TOXICITY": {},
            "IDENTITY_ATTACK": {},
            "INSULT": {},
            "PROFANITY": {},
            "THREAT": {},
        }
    }
    time.sleep(.01)
    response = client.comments().analyze(body=analyze_request, key=api_key).execute()
    
    if 'attributeScores' in response:
        return response['attributeScores']
    else:
        raise Exception(f'Error: {json.dumps(response, indent=2)}')



In [8]:
# Initialize an empty DataFrame to store results
results_df = pd.DataFrame(columns=['tweet', 'language', 'SEVERE_TOXICITY','TOXICITY', 'IDENTITY_ATTACK', 'INSULT', 'PROFANITY', 'THREAT'])


In [9]:

total_tweets = len(sample_df['text'])
update_frequency = 100  # Update the progress every 100 iterations

sample_df.reset_index(drop=True, inplace=True)

for i, row in sample_df.iterrows():
    tweet = row['text']
    language = row['language']
    
    try:
        if (i + 1) % update_frequency == 0:
            print(f'Index: {i}, Progress: {i + 1}/{total_tweets}')
        if language in ["ar", "zh", "cs", "nl", "en", "fr", "de", "hi", "id", "it", "ja", "ko", "pl", "pt", "ru", "es", "sv"]:
            current_api_key = next(api_key_cycle)  # Get the next API key from the iterator
            client = discovery.build(
                "commentanalyzer",
                "v1alpha1",
                developerKey=current_api_key,
                discoveryServiceUrl="https://commentanalyzer.googleapis.com/$discovery/rest?version=v1alpha1",
                static_discovery=False,
            )
            result = call_perspective_api(tweet, client, current_api_key, language=language)

            # Extract the desired attributes from the result
            attributes = {k: result[k]['summaryScore']['value'] for k in result.keys()}
            for attr, value in attributes.items():
                sample_df.at[i, attr] = value
            # Append the result to the DataFrame
            new_row = pd.DataFrame({
                'tweet': [tweet],
                'language': [language],
                **attributes
            })
            results_df = pd.concat([results_df, new_row], ignore_index=True)
        else:
            print(f'Unsupported or unknown language {language} for tweet: {tweet}')
            print("============================================================")
    except Exception as e:
        print(f'Error processing tweet: {tweet}, Error: {e}')
        print("============================================================")




Unsupported or unknown language iw for tweet: לך לזיין את עצמך, פוטין!
(Hebrew)

#FuckPutin #RussiaWarCrimes #RussiaInvadedUkraine #IStandWithUkraine
Unsupported or unknown language uk for tweet: Давайте скинемось мені на стоматкабінет на Оболоні.
Unsupported or unknown language uk for tweet: Починати треба з парасенка🤗 https://t.co/VSs4fz3JbI
Unsupported or unknown language uk for tweet: Ви мабуть вже знаєте про дебілів з Києва які поїли та качали дівчат наркотиками та гвалтували їх.

Так от.

Сьогодні їм вручили повістки.

Це що виходить що передова це тепер табір для тих хто порушує закон?

Такі тварі мають сидіти у в'язниці а не воювати на фронті.
Unsupported or unknown language uk for tweet: 1 вересня розпочалось із школоти, яка під гітарку розспівує кацапські пісні 90-х.
Unsupported or unknown language uk for tweet: Невдала атака росіян під Соледаром

#ЗСУ #Соледар #Бахмут #Україна #Soledar #Bakhmut #Ukraine https://t.co/Iec09qYbPh
Unsupported or unknown language tr for tweet: #U

Index: 199, Progress: 200/150000
Unsupported or unknown language und for tweet: @RpsAgainstTrump #StandWithUkraine
Unsupported or unknown language uk for tweet: @anestesist1 @vkrainets Ну я особисто ще минулого літа розумів що Херсон ще відвоюємо. Бо русні було дуже важко його тримати. https://t.co/ijEQh69x8v
Unsupported or unknown language und for tweet: #RussiaIsATerroristState https://t.co/5qGwvfbS1R
Unsupported or unknown language in for tweet: Wiki 2 tu baada ya kujiunga na NATO, #Finland ilianza kujenga uzio kwenye mpaka na Shirikisho la Urusi, - AP
Kwa mujibu wa Shirika la Habari la Associated Press, wiki mbili baada ya kujiunga na #NATO, https://t.co/DzS02GuqWo
Unsupported or unknown language tr for tweet: Golden cinderella's🍄
https://t.co/kd0WwRF2I5

#mushrooms #CannabisCommunity #COACHELLA2023 #XboxFreeCodeFriday #Ukraine #drugtwt #psychedelics
#depression #MoneyTalks https://t.co/os6gvS8Xy5
Unsupported or unknown language und for tweet: #อิงล็อต #المنطقة_الخضراء #العراق #VMA

Unsupported or unknown language und for tweet: @dengden28841731 
 #dengss #usa #america #canada #uk #love #newyork #instagram #california #travel #instagood #fashion #photography #australia #india #germany #trump #london  #dubai #france #europe #like #art #miami ...
Unsupported or unknown language und for tweet: @Gerashchenko_en 😥🙏 #RussiaIsATerroristState
Unsupported or unknown language und for tweet: #LUCAS
https://t.co/GhyGhmHP9d
Unsupported or unknown language eu for tweet: Iru fiki vin, putin!
(Esperanto)

#FuckPutin #RussiaWarCrimes #IStandWithUkraine #UkraineRussiaWar
Unsupported or unknown language tr for tweet: Marketimize usta kasap ariyoruz
#Almanya #Hessen #Kassel #Germany
https://t.co/EECvpfTBVa
Unsupported or unknown language und for tweet: #SlavaUkraini 
#DefeatPutin https://t.co/AizS4AQHdN
Unsupported or unknown language und for tweet: Russia expects experts from IAEA to visit Zaporozhye NPP #Russia #ZaporozhyeNPP 

https://t.co/Lek3Nvc16S
Unsupported or unknown languag

Unsupported or unknown language und for tweet: @d52NbdYBSYWKUY4 #USOpen
Unsupported or unknown language ro for tweet: "BRUTAL ATTACK (Aug 31) Ukraine special forces destroy hundreds Russian paratroopers in city Kadiivka" #Ukraine  https://t.co/00CT3cHAZl
Unsupported or unknown language uk for tweet: Ще-ще-ще!!!!! https://t.co/76vaBXurdq
Unsupported or unknown language uk for tweet: Гандони штопані
#RussiaIsATerroristState #russiaIsGandonyYobaniState
Unsupported or unknown language et for tweet: “Jumpsuit with train @celineofficial โดย Hedi Slimane ถูกสร้างขึ้นเพื่อลิซ่า 
ในงานประกาศผลรางวัล
MTV Video Music Awards 2022
#VMAs @vmas
โดยเฉพาะ !!! 

LISA WIN BEST K-POP VMAs
LISA Celine Global Ambassador
LISA I'M STILL IN CELINE
#LalisaVMAsWin
#LISA #LISAXCELINE https://t.co/Xhna9uSggG
Unsupported or unknown language und for tweet: @F1 @ShwartzmanRob @ScuderiaFerrari #RussiaIsATerroristState
Unsupported or unknown language ro for tweet: Am văzut ieri seară meciul Simonei Halep de la #USOpen 

Unsupported or unknown language und for tweet: #Россия #зима #мир #Russia #winter #peace https://t.co/D9cUYcR3wS
Unsupported or unknown language tr for tweet: @NedretErsanel Bütün baskıcı liderler toplanmış. Ortak noktaları hepsinin halkı fakir. Hepsinde ekonomiler rezalet. Hepsinde halkın özgürlükleri yerlerde. Hepsinde liderler sultan gibi yaşıyorlar. Sorun baktığında ne gördüğündür. Sorun Türkiye'nin bu leş kargaları ile ne işinin olduğudur.
Unsupported or unknown language und for tweet: #G20Indonesia 👏✍️ https://t.co/C5ykTOT5Zx
Unsupported or unknown language uk for tweet: 🔱 росіяни будуть помирати, навіть не розуміючи від кого та звідки 😈

#україна #stoprussia https://t.co/6Lwdp5TVR5
Unsupported or unknown language und for tweet: @NataliiaKulak #UkraineWillWin https://t.co/koiA9lzeWW
Unsupported or unknown language uk for tweet: @how_2_exist У варусі
Unsupported or unknown language und for tweet: #Blinken #CentralAsia #RussiaIsLosing https://t.co/OSUf5ZzVo7
Unsupported or unknown 

...

Unsupported or unknown language und for tweet: #Ukraine DAO's #NFT sale👇
Unsupported or unknown language und for tweet: @Terror_Alarm ☹️☹️
Unsupported or unknown language uk for tweet: Як вони заїбали🤦
Unsupported or unknown language und for tweet: #Canada https://t.co/h0wPB4blUz
Unsupported or unknown language uk for tweet: поясніть чому під гештегом #Zelensky люди постять якийсь максимально проруснявий крінж?
Unsupported or unknown language und for tweet: @MelnykAndrij #BoycottRussianSport  #RussiaIsATerroristState
Unsupported or unknown language und for tweet: #RussiaIsATerroristState https://t.co/FepeHTNKW5
Unsupported or unknown language eu for tweet: Desfile de Olentzero 2022 en Pamplona/Iruña":

https://t.co/1CSXFsRgUh

#COVID19 #Covid_19 #COVIDー19 #Covid #UkraineRussiaWar @jjaranaz94 #Nochevieja #FelizNavidad #MerryChristmas #FelicesReyes #Feliz2023 #FelizAnoNuevo #FelizAno2023 #misganasganan #Risto #FelizMiercoles #TEVDA https://t.co/wtwUoCq2Qu
Unsupported or unknown language 

Unsupported or unknown language und for tweet: #stoprussiaNow https://t.co/MNeHROt7ZC
Unsupported or unknown language uk for tweet: @c9Tik @GamewayUA В хбох сторі для консолі дешевше для України?
Unsupported or unknown language und for tweet: Russia का वॉर एक्सरसाइज, यूक्रेन की हवा टाइट! | Putin | Ukraine | Nuclear war | NATO | WW3 | America
#Russia #Ukraine #America #China #TrumpIndicted https://t.co/pR2X27GlJE
Unsupported or unknown language uk for tweet: ЦІКАВА ТЕМА.
але ще більш цікава аналітика. https://t.co/uCvdzrIWj0
Unsupported or unknown language in for tweet: KTT G20 Wilayah Kerja Kanwil Kemenkumham Jateng https://t.co/sZK10iRB6Q

@Kemenkumham_RI @bhp_semarang #bhpsemarang #KumhamPasti #KamiPasti #KumhamSemakinPasti #Kumham #kemenkumham #kemenkumhamari #Berita #Twitter #KanwilKemenkumhamJateng #G20BangkitLebihKuat #G20Indonesia
Unsupported or unknown language und for tweet: 🌻#StandWithUkraine #StopRussia #PutinAtWar #UkraineRussia #WarinUkraine #EU #Kherson #ArmUkraineNow #NA

Index: 121899, Progress: 121900/150000
Unsupported or unknown language und for tweet: @RpsAgainstTrump #StandWithUkraine
Unsupported or unknown language te for tweet: మీరే ఫక్, పుతిన్!
(Telugu)

#StopPutin #PutinWarCrimes #RussianWarCrimes #FuckPutin
Unsupported or unknown language uk for tweet: @Mafia_870 Спочатку людина мене газлайтить, ненавидить, доводить до дурки  і бажає смерті, а потім змінює думку?)))))
Ага, так)))
Unsupported or unknown language und for tweet: #Germany 🤣😂🤣😂🤣😂🤣😂🤣😂🤣😂🤣😂🤣😂🤣😂🤣😂😂😂🤣 https://t.co/ZF1mbXiy55
Unsupported or unknown language uk for tweet: @fruityjarpad Дякую😭💕
Unsupported or unknown language und for tweet: #2504 #quote #NFT #love #war https://t.co/6mVcW0XPuz
Unsupported or unknown language uk for tweet: @riya_capable дякуююю https://t.co/mYVxEK5zqF
Unsupported or unknown language in for tweet: terimakasih sudah memberikan yg terbaik versi kalian. terimakasih sudah berjuang dgn baik! kalian tetap jdi yg terbaik! #Jerman #DieMannschaft #DerPanzer #Germany 

Unsupported or unknown language is for tweet: Farðu í þig, Pútín!
(Icelandic)

#RussiaWarCrimes #RussiaInvadedUkraine #RussianWarCrimes #UkraineUnderAttack
Unsupported or unknown language uk for tweet: @galmalivoruch треба в страхової попитать, які вакцини покривають, і хоч щось від них взяти)))
Unsupported or unknown language und for tweet: #OpRussia #Ukraine #UkraineRussiaWar #PutinIsaWarCriminal #FckPutin #Anonymous @ITArmyUKR
#SlavaUkraini #SlavaUkraine https://t.co/G95QRlZIGh
Unsupported or unknown language uk for tweet: @mixvoronezh Да з єбалами якась хуйня робиться...
Unsupported or unknown language uk for tweet: Зате готовий вмирати🤦🏻‍♂️
Краще вже б підірвав себе разом із воєнкомом. https://t.co/vVeS0HPc3p
Unsupported or unknown language und for tweet: #dorothyjeanius #intelligent #determination #trialblazer #accomplishment #motivation #inspiration #rolemodel #stem #dedication #hardwork #chicagouniversity #usa #uk #canada #nigeria #africa #world #espact
Unsupported or unknown l

Unsupported or unknown language uk for tweet: 💥 Повідомляють про вибухи у #Бердянську

Перевіряємо.


In [10]:
print(results_df.head())
print(results_df.shape)
# 25k - however many non supported languages in 9 columns with attributes and tweets
results_df.to_csv('results150000short0819t0506.csv', index=False)
# 25k random with other columns
sample_df.to_csv('results150000long0819t0506.csv', index=False)
print(sample_df.shape)

{
  "TOXICITY": {
    "spanScores": [
      {
        "begin": 0,
        "end": 74,
        "score": {
          "value": 0.015770407,
          "type": "PROBABILITY"
        }
      }
    ],
    "summaryScore": {
      "value": 0.015770407,
      "type": "PROBABILITY"
    }
  },
  "INSULT": {
    "spanScores": [
      {
        "begin": 0,
        "end": 74,
        "score": {
          "value": 0.008538882,
          "type": "PROBABILITY"
        }
      }
    ],
    "summaryScore": {
      "value": 0.008538882,
      "type": "PROBABILITY"
    }
  },
  "PROFANITY": {
    "spanScores": [
      {
        "begin": 0,
        "end": 74,
        "score": {
          "value": 0.015215653,
          "type": "PROBABILITY"
        }
      }
    ],
    "summaryScore": {
      "value": 0.015215653,
      "type": "PROBABILITY"
    }
  },
  "THREAT": {
    "spanScores": [
      {
        "begin": 0,
        "end": 74,
        "score": {
          "value": 0.007857903,
          "type": "PROBABIL

In [10]:
# TESTING SINGULAR API 
import requests
import IPython.display as display
from googleapiclient import discovery
import json
import time
from langdetect import detect
import pandas as pd
import numpy as np
tweet = "DON'T SHOW YOUR BEAUTY #shorts https://t.co/DrDBcM77jA #Ukraine #NEARProtocol #twitter did you know"
client = discovery.build(
                "commentanalyzer",
                "v1alpha1",
                developerKey="",
                discoveryServiceUrl="https://commentanalyzer.googleapis.com/$discovery/rest?version=v1alpha1",
                static_discovery=False,
            )
result = call_perspective_api(tweet, client, "", "en")


In [11]:
result

{'SEVERE_TOXICITY': {'spanScores': [{'begin': 0,
    'end': 99,
    'score': {'value': 0.011291504, 'type': 'PROBABILITY'}}],
  'summaryScore': {'value': 0.011291504, 'type': 'PROBABILITY'}},
 'INSULT': {'spanScores': [{'begin': 0,
    'end': 99,
    'score': {'value': 0.054376744, 'type': 'PROBABILITY'}}],
  'summaryScore': {'value': 0.054376744, 'type': 'PROBABILITY'}},
 'IDENTITY_ATTACK': {'spanScores': [{'begin': 0,
    'end': 99,
    'score': {'value': 0.0376521, 'type': 'PROBABILITY'}}],
  'summaryScore': {'value': 0.0376521, 'type': 'PROBABILITY'}},
 'TOXICITY': {'spanScores': [{'begin': 0,
    'end': 99,
    'score': {'value': 0.18649188, 'type': 'PROBABILITY'}}],
  'summaryScore': {'value': 0.18649188, 'type': 'PROBABILITY'}},
 'THREAT': {'spanScores': [{'begin': 0,
    'end': 99,
    'score': {'value': 0.020954676, 'type': 'PROBABILITY'}}],
  'summaryScore': {'value': 0.020954676, 'type': 'PROBABILITY'}},
 'PROFANITY': {'spanScores': [{'begin': 0,
    'end': 99,
    'score': 